In [1]:
import json
from pathlib import Path

import albumentations as A
import cv2
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from PIL import Image

In [2]:
# width or x - горизонталь
# height or y - вертикаль
# Each row is - class x_center y_center width height format.
# Box coordinates must be in normalized xywh format (from 0 - 1). If your boxes are in pixels, divide x_center and width by image width, and y_center and height by image height.
# Class numbers are zero-indexed (start from 0).
# пример строки в файле .txt - '45 0.479492 0.688771 0.955609 0.5955\n'

In [3]:
def get_files(files_dir: Path, suff: str = 'txt') -> list[Path]:
    return sorted(Path(files_dir).glob(f'*.{suff}'))


# Преобразование координат объектов в формат yolo

## Загрузка координат в pandas

In [4]:
location_csv = Path('../train_dataset_train/train.csv')
location_image = Path('../train_dataset_train/train')
location_labels = Path('../train_dataset_train/labels')

In [5]:
location = pd.read_csv(location_csv)

In [6]:
location.insert(3, 'short_name', ['']*location.shape[0])

In [7]:
def insert_short_name(x):    
    x['short_name'] = str(x['ID_img']).split('.')[0]
    return x

In [8]:
location = location.apply(insert_short_name, axis=1)

In [9]:
location

ID_img  count_region region_shape short_name
0     3436.JPG           0.0          0.0       3436
1     3437.JPG           0.0          0.0       3437
2     3438.JPG           0.0          0.0       3438
3     3439.JPG           0.0          0.0       3439
4     3440.JPG           0.0          0.0       3440
...        ...           ...          ...        ...
5157  8593.JPG           0.0          0.0       8593
5158  8594.JPG           0.0          0.0       8594
5159  8595.JPG           0.0          0.0       8595
5160  8596.JPG           0.0          0.0       8596
5161  8597.JPG           0.0          0.0       8597

[5162 rows x 4 columns]

In [10]:
location[location['region_shape'] != '0.0']

ID_img  count_region  \
8     3444.jpg           1.0   
217   3653.JPG           1.0   
254   3690.JPG           1.0   
399   3835.JPG           2.0   
511   3947.JPG           1.0   
717   4153.jpg           1.0   
833   4269.JPG           6.0   
855   4291.JPG           2.0   
1029  4465.JPG           2.0   
1168  4604.JPG           2.0   
1344  4780.JPG           2.0   
1435  4871.jpg           1.0   
1452  4888.JPG           2.0   
1498  4934.JPG           2.0   
1629  5065.JPG           2.0   
1755  5191.JPG           2.0   
1841  5277.JPG           2.0   
1878  5314.JPG           2.0   
2042  5478.JPG           2.0   
2244  5680.jpg           1.0   
2388  5824.JPG           2.0   
2520  5956.JPG           4.0   
2669  6105.JPG           2.0   
2710  6146.JPG           2.0   
2717  6153.JPG           2.0   
2783  6219.JPG           1.0   
2785  6221.JPG           2.0   
2797  6233.JPG           2.0   
2932  6368.JPG           2.0   
3042  6478.jpg          10.0   
3125  6561.JPG           5.0   
3248  6684.JPG           1.0   
3278  6714.jpg           1.0   
3305  6741.JPG           5.0   
3418  6854.JPG           2.0   
3470  6906.JPG           3.0   
3472  6908.JPG           2.0   
3475  6911.JPG           2.0   
3576  7012.JPG           5.0   
3613  7049.JPG           2.0   
3642  7078.JPG           2.0   
3764  7200.JPG           3.0   
3827  7263.JPG           1.0   
4141  7577.JPG           2.0   
4277  7713.JPG           3.0   
4286  7722.JPG           2.0   
4436  7872.JPG           1.0   
4584  8020.jpg           1.0   
4612  8048.JPG           1.0   
4667  8103.JPG           2.0   
4711  8147.JPG           2.0   
4719  8155.JPG           1.0   
4782  8218.JPG           4.0   
4821  8257.JPG           2.0   
4944  8380.JPG           2.0   
4970  8406.jpg           4.0   
5028  8464.JPG           1.0   
5071  8507.JPG           2.0   

                                           region_shape short_name  
8                       ['{"cx":2259,"cy":391,"r":64}']       3444  
217                    ['{"cx":2719,"cy":2097,"r":75}']       3653  
254                    ['{"cx":2914,"cy":1693,"r":90}']       3690  
399   ['{"cx":2549,"cy":2329,"r":80}', '{"cx":2437,"...       3835  
511                   ['{"cx":3130,"cy":1370,"r":134}']       3947  
717                    ['{"cx":3731,"cy":3049,"r":75}']       4153  
833   ['{"cx":3575,"cy":1657,"r":98}', '{"cx":3284,"...       4269  
855   ['{"cx":3467,"cy":1740,"r":77}', '{"cx":3587,"...       4291  
1029  ['{"cx":2735,"cy":1711,"r":102}', '{"cx":2430,...       4465  
1168  ['{"cx":3276,"cy":1619,"r":130}', '{"cx":3114,...       4604  
1344  ['{"cx":3898,"cy":988,"r":123}', '{"cx":3309,"...       4780  
1435                  ['{"cx":1219,"cy":1005,"r":105}']       4871  
1452  ['{"cx":2188,"cy":244,"r":91}', '{"cx":2237,"c...       4888  
1498  ['{"cx":2890,"cy":775,"r":110}', '{"cx":3045,"...       4934  
1629  ['{"cx":1167,"cy":1568,"r":36}', '{"cx":1268,"...       5065  
1755  ['{"cx":2346,"cy":2840,"r":93}', '{"cx":2217,"...       5191  
1841  ['{"cx":3321,"cy":924,"r":50}', '{"cx":3277,"c...       5277  
1878  ['{"cx":2566,"cy":1250,"r":121}', '{"cx":2616,...       5314  
2042  ['{"cx":3135,"cy":1827,"r":121}', '{"cx":3006,...       5478  
2244                  ['{"cx":2765,"cy":1998,"r":109}']       5680  
2388  ['{"cx":2902,"cy":1824,"r":102}', '{"cx":2854,...       5824  
2520  ['{"cx":2678,"cy":1640,"r":77}', '{"cx":2570,"...       5956  
2669  ['{"cx":2807,"cy":1603,"r":84}', '{"cx":2736,"...       6105  
2710  ['{"cx":3226,"cy":1030,"r":94.856}', '{"cx":33...       6146  
2717  ['{"cx":2193,"cy":2053,"r":95}', '{"cx":2092,"...       6153  
2783                  ['{"cx":2408,"cy":2304,"r":125}']       6219  
2785  ['{"cx":3193,"cy":1715,"r":88}', '{"cx":3394,"...       6221  
2797  ['{"cx":4197,"cy":1489,"r":87}', '{"cx":4299,"...       6233  
2932  ['{"cx":1553,"cy":2047,"r":103}', '{"cx":2105,...       6368  
3042  ['{"cx":2466,"cy":1079,"r":82}', '{"cx":230

In [11]:
def get_size(image_file: Path) -> tuple[int, int]:
    forest_image = Image.open(image_file)
    width, height = forest_image.size
    return width, height

In [12]:
def get_fraction(image_size: tuple[int, int], location: list[dict[str, int]]) -> list[list[float]]:
    # location consist: 
    # ‘r’ - область внутри которой находиться человек
    # ‘cx’ - центр окружности по координате x
    # ‘cy’ - центр окружности по координате y
    boxes = []
    width, height = image_size
    for box in location:        
        center_x = str(box['cx'] / width)
        center_y = str(box['cy'] / height)
        box_width = str(box['r'] / width)
        box_height = str(box['r'] / height)
        boxes.append(['0', center_x, center_y, box_width, box_height])
    return boxes


In [13]:
def get_text(boxes: list[list[float]]) -> list[str]:
    boxes_str = []
    for location in boxes:
        new_line = ' '.join(location) + '\n'
        boxes_str.append(new_line)
    return boxes_str

In [14]:
def write_txt(boxes: list[str], name: str) -> None:
    txt_file = location_labels / f'{name}.txt'
    with open(txt_file, 'w') as new_file:
        for row in boxes:
            new_file.write(row)

In [15]:
def row_handler(row: pd.Series) -> None:
    #print(type(row))
    name, coord = row['ID_img'], row['region_shape']
    short_name = name.split('.')[0]
    boxes = json.loads(coord.replace("\'", ""))
    image_file = location_image / name
    size = get_size(image_file)
    boxes = get_fraction(size, boxes)
    boxes = get_text(boxes)
    write_txt(boxes, short_name)
    #print(boxes)

image_file = Path('../train_dataset_train/train/3771.JPG')
size = get_size(image_file)
size

coord = location.iloc[395]['region_shape']
boxes = json.loads(coord.replace("\'", ""))
boxes = get_fraction(size, boxes)
boxes = get_text(boxes)
boxes

In [16]:
# исключаем строки где нет людей и преобразуем координаты в текстовый файл
location[location['region_shape'] != '0.0'].apply(row_handler, axis=1)

8       None
217     None
254     None
399     None
511     None
717     None
833     None
855     None
1029    None
1168    None
1344    None
1435    None
1452    None
1498    None
1629    None
1755    None
1841    None
1878    None
2042    None
2244    None
2388    None
2520    None
2669    None
2710    None
2717    None
2783    None
2785    None
2797    None
2932    None
3042    None
3125    None
3248    None
3278    None
3305    None
3418    None
3470    None
3472    None
3475    None
3576    None
3613    None
3642    None
3764    None
3827    None
4141    None
4277    None
4286    None
4436    None
4584    None
4612    None
4667    None
4711    None
4719    None
4782    None
4821    None
4944    None
4970    None
5028    None
5071    None
dtype: object

# Аугументация датасета

In [17]:
aug_dir = Path('../train_dataset_train/augumentation')
aug_size = 256

In [18]:
labels_list = get_files(location_labels)

In [19]:
transform_person = A.Compose(
    [A.RandomSizedBBoxSafeCrop(width=aug_size, height=aug_size, erosion_rate=0.3)],
    bbox_params=A.BboxParams(format='yolo', label_fields=['class_labels']),
)

In [20]:
transform_area = A.Compose([
    A.RandomCrop(width=aug_size, height=aug_size),
    A.HorizontalFlip(p=0.5),
    A.RandomBrightnessContrast(p=0.2),
], bbox_params=A.BboxParams(format='yolo', min_visibility=0.2, label_fields=['class_labels']))

In [21]:
def transformer_person(image, bboxes, class_labels):
    transformed = transform_person(image=image, bboxes=bboxes, class_labels=class_labels)
    transformed_image = transformed['image']
    transformed_bboxes = transformed['bboxes']
    transformed_class_labels = transformed['class_labels']    
    return transformed_image, transformed_bboxes

In [22]:
def transformer_area(image, bboxes, class_labels):
    transformed = transform_area(image=image, bboxes=bboxes, class_labels=class_labels)
    transformed_image = transformed['image']
    transformed_bboxes = transformed['bboxes']
    transformed_class_labels = transformed['class_labels']    
    return transformed_image, transformed_bboxes

In [23]:
def read_boxes(label_path: Path) -> list[str]:
    with open(label_path, 'r') as label:
        label_list = label.readlines()
    return label_list

In [24]:
def get_image(image_path: Path):
    #image = Image.open(image_path)
    image = cv2.imread(str(image_path))
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    return image

In [25]:
def get_boxes(label_path: Path) -> tuple[list[float], list[str]]:
    boxes = read_boxes(label_path)
    boxes_list = []
    labels = []
    for box in boxes:
        box = box.replace('\n', '')
        box = box.split(' ')
        # срезаем до 8 знаков после запятой
        bbox = [float(x[:11]) for x in box[1:]]
        boxes_list.append(bbox)
        labels.append(box[0])
    return boxes_list, labels

In [26]:
def save_image(image, name: str) -> None:
    image_path = aug_dir / 'images' / f'{name}.jpg'
    cv2.imwrite(str(image_path), image)

In [27]:
def write_txt(boxes: list[str], name: str) -> None:
    txt_file = aug_dir / 'labels' / f'{name}.txt'
    with open(txt_file, 'w') as new_file:
        for row in boxes:
            new_file.write(row)

In [28]:
def save_label(boxes: list, name: str) -> None:
    rows = []
    for box in boxes:
        row = ' '.join([f'{x}' for x in box])
        row = '0 ' + row + '\n'
        rows.append(row)
    write_txt(rows, name)
        

In [29]:
def show_image(image, mask):
    if len(mask) > 0:
        fig, axes = plt.subplots(nrows=1, ncols=2, figsize=(25,25))
        axes[0].imshow(image)
        #axes[1].imshow(mask[..., 0])
        plt.show

In [30]:
BOX_COLOR = (255, 0, 0) # Red
TEXT_COLOR = (255, 255, 255) # White

def visualize_bbox(img, bbox, class_name, color=(250,0,0), thickness=1):
    """Visualizes a single bounding box on the image"""
    print(img.shape)
    x_c, y_min, w, h = bbox
    x_min, x_max, y_min, y_max = int(x_c*256-(w*256)), int(x_c*256 + (w*256)), int(y_min*256-(h*256)), int(y_min*256 + (h*256))
   
    cv2.rectangle(img, (x_min, y_min), (x_max, y_max), color=color, thickness=thickness)
    
    ((text_width, text_height), _) = cv2.getTextSize(class_name, cv2.FONT_HERSHEY_SIMPLEX, 0.25, 1)    
    cv2.rectangle(img, (x_min, y_min - int(1.3 * text_height)), (x_min + text_width, y_min), BOX_COLOR, -1)
    cv2.putText(
        img,
        text=class_name,
        org=(x_min, y_min - int(0.3 * text_height)),
        fontFace=cv2.FONT_HERSHEY_SIMPLEX,
        fontScale=0.35, 
        color=TEXT_COLOR, 
        lineType=cv2.LINE_AA,
    )
    return img

def visualize(image, bboxes, category_ids=['0'], category_id_to_name={'0': 'person'}):
    img = image.copy()
    
    for bbox, category_id in zip(bboxes, category_ids):
        class_name = category_id_to_name[category_id]
        img = visualize_bbox(img, bbox, class_name)
    plt.figure(figsize=(12, 12))
    plt.axis('off')
    plt.imshow(img)

In [31]:
def start_aug():
    errors_box = 0
    for numer, label_file in enumerate(labels_list):
        short_name = label_file.stem
        image_name = location[location['short_name']==short_name]['ID_img'].values[0]
        image_path = location_image / image_name
        image = get_image(image_path)
        bboxes, class_labels = get_boxes(label_file)
        
        for num in range(300):
            name = f'{short_name}p{num}'
            try:
                new_image, new_bboxes = transformer_person(image, bboxes, class_labels)
                #print(bboxes, new_bboxes)
                category_ids = ['0']* len(new_bboxes)
                #visualize(new_image, new_bboxes, category_ids)
                save_image(new_image, name)
                save_label(new_bboxes, name)
            except:
                errors_box += 1
            
        for num in range(400):
            name = f'{short_name}a{num}'
            try:
                new_image, new_bboxes = transformer_area(image, bboxes, class_labels)
                category_ids = ['0'] * len(new_bboxes)
                #visualize(new_image, new_bboxes, category_ids)
                save_image(new_image, name)
                if len(new_bboxes) > 0:
                    save_label(new_bboxes, name)
            except:
                errors_box += 1
            
        print(numer)
    print(errors_box)

In [32]:
start_aug()

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
0


In [33]:
location[location['region_shape'] != '0.0'].shape

(58, 4)

In [34]:
len(labels_list)

58

# Создание набора тестовых и тренироваочных даных


In [35]:
crop_image = aug_dir / 'images'
crop_labels = aug_dir / 'labels'

In [36]:
crop_image_list = get_files(crop_image, 'jpg')
crop_labels_list = get_files(crop_labels)


In [37]:
crop_labels_list = [Path(label_path).stem for label_path in crop_labels_list]
#crop_labels_list

In [38]:
dataset_df = pd.DataFrame(columns=['image', 'label', 'image_path', 'label_path'])

In [39]:
dataset_df['image_path'] = crop_image_list

In [40]:
dataset_df

image label                                         image_path  \
0       NaN   NaN  ../train_dataset_train/augumentation/images/34...   
1       NaN   NaN  ../train_dataset_train/augumentation/images/34...   
2       NaN   NaN  ../train_dataset_train/augumentation/images/34...   
3       NaN   NaN  ../train_dataset_train/augumentation/images/34...   
4       NaN   NaN  ../train_dataset_train/augumentation/images/34...   
...     ...   ...                                                ...   
40595   NaN   NaN  ../train_dataset_train/augumentation/images/85...   
40596   NaN   NaN  ../train_dataset_train/augumentation/images/85...   
40597   NaN   NaN  ../train_dataset_train/augumentation/images/85...   
40598   NaN   NaN  ../train_dataset_train/augumentation/images/85...   
40599   NaN   NaN  ../train_dataset_train/augumentation/images/85...   

      label_path  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  
...          ...  
40595        NaN  
40596        NaN  
40597        NaN  
40598        NaN  
40599        NaN  

[40600 rows x 4 columns]

In [41]:
def path_to_name(row: pd.Series) -> pd.Series:
    image = Path(row['image_path'])
    row['image'] = image.name
    if image.stem in crop_labels_list:
        row['label'] = f'{image.stem}.txt'
        row['label_path'] = aug_dir / 'labels' /row['label']
    return row

In [42]:
dataset_df.apply(path_to_name, axis=1)

image        label  \
0        3444a0.jpg          NaN   
1        3444a1.jpg          NaN   
2       3444a10.jpg          NaN   
3      3444a100.jpg          NaN   
4      3444a101.jpg          NaN   
...             ...          ...   
40595   8507p95.jpg  8507p95.txt   
40596   8507p96.jpg  8507p96.txt   
40597   8507p97.jpg  8507p97.txt   
40598   8507p98.jpg  8507p98.txt   
40599   8507p99.jpg  8507p99.txt   

                                              image_path  \
0      ../train_dataset_train/augumentation/images/34...   
1      ../train_dataset_train/augumentation/images/34...   
2      ../train_dataset_train/augumentation/images/34...   
3      ../train_dataset_train/augumentation/images/34...   
4      ../train_dataset_train/augumentation/images/34...   
...                                                  ...   
40595  ../train_dataset_train/augumentation/images/85...   
40596  ../train_dataset_train/augumentation/images/85...   
40597  ../train_dataset_train/augumentation/images/85...   
40598  ../train_dataset_train/augumentation/images/85...   
40599  ../train_dataset_train/augumentation/images/85...   

                                              label_path  
0                                                    NaN  
1                                                    NaN  
2                                                    NaN  
3                                                    NaN  
4                                                    NaN  
...                                                  ...  
40595  ../train_dataset_train/augumentation/labels/85...  
40596  ../train_dataset_train/augumentation/labels/85...  
40597  ../train_dataset_train/augumentation/labels/85...  
40598  ../train_dataset_train/augumentation/labels/85...  
40599  ../train_dataset_train/augumentation/labels/85...  

[40600 rows x 4 columns]

In [43]:
dataset_df

image        label  \
0        3444a0.jpg          NaN   
1        3444a1.jpg          NaN   
2       3444a10.jpg          NaN   
3      3444a100.jpg          NaN   
4      3444a101.jpg          NaN   
...             ...          ...   
40595   8507p95.jpg  8507p95.txt   
40596   8507p96.jpg  8507p96.txt   
40597   8507p97.jpg  8507p97.txt   
40598   8507p98.jpg  8507p98.txt   
40599   8507p99.jpg  8507p99.txt   

                                              image_path  \
0      ../train_dataset_train/augumentation/images/34...   
1      ../train_dataset_train/augumentation/images/34...   
2      ../train_dataset_train/augumentation/images/34...   
3      ../train_dataset_train/augumentation/images/34...   
4      ../train_dataset_train/augumentation/images/34...   
...                                                  ...   
40595  ../train_dataset_train/augumentation/images/85...   
40596  ../train_dataset_train/augumentation/images/85...   
40597  ../train_dataset_train/augumentation/images/85...   
40598  ../train_dataset_train/augumentation/images/85...   
40599  ../train_dataset_train/augumentation/images/85...   

                                              label_path  
0                                                    NaN  
1                                                    NaN  
2                                                    NaN  
3                                                    NaN  
4                                                    NaN  
...                                                  ...  
40595  ../train_dataset_train/augumentation/labels/85...  
40596  ../train_dataset_train/augumentation/labels/85...  
40597  ../train_dataset_train/augumentation/labels/85...  
40598  ../train_dataset_train/augumentation/labels/85...  
40599  ../train_dataset_train/augumentation/labels/85...  

[40600 rows x 4 columns]

In [44]:
label_df = dataset_df[dataset_df['label'].notna()].copy()
non_label_df = dataset_df[dataset_df['label'].isna()].copy()

In [45]:
label_df.head(2)

image         label  \
11  3444a108.jpg  3444a108.txt   
21  3444a117.jpg  3444a117.txt   

                                           image_path  \
11  ../train_dataset_train/augumentation/images/34...   
21  ../train_dataset_train/augumentation/images/34...   

                                           label_path  
11  ../train_dataset_train/augumentation/labels/34...  
21  ../train_dataset_train/augumentation/labels/34...

In [46]:
dataset_df.shape[0] - label_df.shape[0] - non_label_df.shape[0]

0

In [47]:
def train_validate_test_split(df: pd.DataFrame, train_percent: float = 0.6, validate_percent: float = 0.4, seed=None):
    np.random.seed(seed)
    perm = np.random.permutation(df.index)
    m = len(df.index)
    train_end = int(train_percent * m)
    validate_end = int(validate_percent * m) + train_end
    train = df.iloc[perm[:train_end]]
    validate = df.iloc[perm[train_end:validate_end]]
    test = df.iloc[perm[validate_end:]]
    return train, validate, test

In [48]:
train_df_1, valid_df_1, _ = train_validate_test_split(label_df.reset_index(drop=True))

In [49]:
train_df_2, valid_df_2, _ = train_validate_test_split(non_label_df.reset_index(drop=True))

In [50]:
train_df = pd.concat([train_df_1, train_df_2])
valid_df = pd.concat([valid_df_1, valid_df_2])

In [51]:
dataset_df.shape, valid_df.shape, train_df.shape

((40600, 4), (16239, 4), (24359, 4))

In [52]:
11595+17393

28988

In [53]:
valid_df

image         label  \
13672   7713p68.jpg   7713p68.txt   
6226   5824p233.jpg  5824p233.txt   
12832  7263p133.jpg  7263p133.txt   
9092    6478p68.jpg   6478p68.txt   
17311   8464p74.jpg   8464p74.txt   
...             ...           ...   
22943   8507a86.jpg           NaN   
14501  6908a337.jpg           NaN   
2580   4269a278.jpg           NaN   
936    3690a227.jpg           NaN   
15852  7078a130.jpg           NaN   

                                              image_path  \
13672  ../train_dataset_train/augumentation/images/77...   
6226   ../train_dataset_train/augumentation/images/58...   
12832  ../train_dataset_train/augumentation/images/72...   
9092   ../train_dataset_train/augumentation/images/64...   
17311  ../train_dataset_train/augumentation/images/84...   
...                                                  ...   
22943  ../train_dataset_train/augumentation/images/85...   
14501  ../train_dataset_train/augumentation/images/69...   
2580   ../train_dataset_train/augumentation/images/42...   
936    ../train_dataset_train/augumentation/images/36...   
15852  ../train_dataset_train/augumentation/images/70...   

                                              label_path  
13672  ../train_dataset_train/augumentation/labels/77...  
6226   ../train_dataset_train/augumentation/labels/58...  
12832  ../train_dataset_train/augumentation/labels/72...  
9092   ../train_dataset_train/augumentation/labels/64...  
17311  ../train_dataset_train/augumentation/labels/84...  
...                                                  ...  
22943                                                NaN  
14501                                                NaN  
2580                                                 NaN  
936                                                  NaN  
15852                                                NaN  

[16239 rows x 4 columns]

In [54]:
import shutil
import os

def move_file(short_name: str, target_dir: str) -> None:
    image_file = aug_dir / 'images' / f'{short_name}.jpg'
    new_image = aug_dir / 'images' / target_dir / f'{short_name}.jpg'
    shutil.move(image_file, new_image)
    
    label_file = aug_dir / 'labels' / f'{short_name}.txt'
    new_label = aug_dir / 'labels' / target_dir / f'{short_name}.txt'
    print(label_file)
    print(new_label)
    print(label_file.is_file())
    if label_file.is_file():
        print('ok')
        shutil.move(label_file, new_label)


In [55]:
def move_handler(row, target_dir):
    name = Path(row['image_path']).stem
    move_file(str(name), target_dir)
    return row

In [57]:
valid_df.apply(move_handler, axis=1, args=('test',))

../train_dataset_train/augumentation/labels/7713p68.txt
../train_dataset_train/augumentation/labels/test/7713p68.txt
True
ok
../train_dataset_train/augumentation/labels/5824p233.txt
../train_dataset_train/augumentation/labels/test/5824p233.txt
True
ok
../train_dataset_train/augumentation/labels/7263p133.txt
../train_dataset_train/augumentation/labels/test/7263p133.txt
True
ok
../train_dataset_train/augumentation/labels/6478p68.txt
../train_dataset_train/augumentation/labels/test/6478p68.txt
True
ok
../train_dataset_train/augumentation/labels/8464p74.txt
../train_dataset_train/augumentation/labels/test/8464p74.txt
True
ok
../train_dataset_train/augumentation/labels/5478p165.txt
../train_dataset_train/augumentation/labels/test/5478p165.txt
True
ok
../train_dataset_train/augumentation/labels/6146p247.txt
../train_dataset_train/augumentation/labels/test/6146p247.txt
True
ok
../train_dataset_train/augumentation/labels/6105p233.txt
../train_dataset_train/augumentation/labels/test/6105p233.tx

image         label  \
13672   7713p68.jpg   7713p68.txt   
6226   5824p233.jpg  5824p233.txt   
12832  7263p133.jpg  7263p133.txt   
9092    6478p68.jpg   6478p68.txt   
17311   8464p74.jpg   8464p74.txt   
...             ...           ...   
22943   8507a86.jpg           NaN   
14501  6908a337.jpg           NaN   
2580   4269a278.jpg           NaN   
936    3690a227.jpg           NaN   
15852  7078a130.jpg           NaN   

                                              image_path  \
13672  ../train_dataset_train/augumentation/images/77...   
6226   ../train_dataset_train/augumentation/images/58...   
12832  ../train_dataset_train/augumentation/images/72...   
9092   ../train_dataset_train/augumentation/images/64...   
17311  ../train_dataset_train/augumentation/images/84...   
...                                                  ...   
22943  ../train_dataset_train/augumentation/images/85...   
14501  ../train_dataset_train/augumentation/images/69...   
2580   ../train_dataset_train/augumentation/images/42...   
936    ../train_dataset_train/augumentation/images/36...   
15852  ../train_dataset_train/augumentation/images/70...   

                                              label_path  
13672  ../train_dataset_train/augumentation/labels/77...  
6226   ../train_dataset_train/augumentation/labels/58...  
12832  ../train_dataset_train/augumentation/labels/72...  
9092   ../train_dataset_train/augumentation/labels/64...  
17311  ../train_dataset_train/augumentation/labels/84...  
...                                                  ...  
22943                                                NaN  
14501                                                NaN  
2580                                                 NaN  
936                                                  NaN  
15852                                                NaN  

[16239 rows x 4 columns]

In [58]:
train_df.apply(move_handler, axis=1, args=('train',))

../train_dataset_train/augumentation/labels/4269p26.txt
../train_dataset_train/augumentation/labels/train/4269p26.txt
True
ok
../train_dataset_train/augumentation/labels/8155p256.txt
../train_dataset_train/augumentation/labels/train/8155p256.txt
True
ok
../train_dataset_train/augumentation/labels/8507p82.txt
../train_dataset_train/augumentation/labels/train/8507p82.txt
True
ok
../train_dataset_train/augumentation/labels/5277p173.txt
../train_dataset_train/augumentation/labels/train/5277p173.txt
True
ok
../train_dataset_train/augumentation/labels/5956p11.txt
../train_dataset_train/augumentation/labels/train/5956p11.txt
True
ok
../train_dataset_train/augumentation/labels/6478p116.txt
../train_dataset_train/augumentation/labels/train/6478p116.txt
True
ok
../train_dataset_train/augumentation/labels/7263p98.txt
../train_dataset_train/augumentation/labels/train/7263p98.txt
True
ok
../train_dataset_train/augumentation/labels/8507p125.txt
../train_dataset_train/augumentation/labels/train/8507p

image         label  \
2003    4269p26.jpg   4269p26.txt   
15696  8155p256.jpg  8155p256.txt   
17623   8507p82.jpg   8507p82.txt   
4941   5277p173.jpg  5277p173.txt   
6393    5956p11.jpg   5956p11.txt   
...             ...           ...   
2821   4291a139.jpg           NaN   
22621  8507a152.jpg           NaN   
9170   6146a149.jpg           NaN   
7045   5314a376.jpg           NaN   
19993  8147a289.jpg           NaN   

                                              image_path  \
2003   ../train_dataset_train/augumentation/images/42...   
15696  ../train_dataset_train/augumentation/images/81...   
17623  ../train_dataset_train/augumentation/images/85...   
4941   ../train_dataset_train/augumentation/images/52...   
6393   ../train_dataset_train/augumentation/images/59...   
...                                                  ...   
2821   ../train_dataset_train/augumentation/images/42...   
22621  ../train_dataset_train/augumentation/images/85...   
9170   ../train_dataset_train/augumentation/images/61...   
7045   ../train_dataset_train/augumentation/images/53...   
19993  ../train_dataset_train/augumentation/images/81...   

                                              label_path  
2003   ../train_dataset_train/augumentation/labels/42...  
15696  ../train_dataset_train/augumentation/labels/81...  
17623  ../train_dataset_train/augumentation/labels/85...  
4941   ../train_dataset_train/augumentation/labels/52...  
6393   ../train_dataset_train/augumentation/labels/59...  
...                                                  ...  
2821                                                 NaN  
22621                                                NaN  
9170                                                 NaN  
7045                                                 NaN  
19993                                                NaN  

[24359 rows x 4 columns]

In [ ]:
short_name = '3444a32__'
target_dir = 'test'
label_file = aug_dir / 'labels' / f'{short_name}.txt'
new_label = aug_dir / 'labels' / target_dir / f'{short_name}.txt'

In [ ]:
label_file.is_file()

In [ ]:
739772